In [ ]:
import opensrane as opr
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from copy import deepcopy

## Liquid Spread considering gas dispersion (LqdSprdGuassianGasDisp)

In [ ]:
#Verification by casal example 2.9
opr.wipe()

SiteTAg=1
opr.Sites.Site(SiteTAg, Temperature=20+273,Pressure=1.0132*10**5 ,XSiteBoundary=[0,100,100,0], YSiteBoundary=[0,0,100,100], g=9.81)


#Create Wind Object
windobj=opr.WindData.WindRose(tag=1)
windobj.WindClass="A"
windobj.WindDirection=90
windobj.WindSpeed=3
windobj.AlphaCOEF=1
windobj.isCalmn=False


#Define Material
subsObj=opr.Substance.DataBank.CasCalEx2_1(1)
subsObj.Specific_Heat_of_Vaporization=392.23*1000
subsObj.Vapour_Pressure=16130                      #Accoring Casal Example 2.9
subsObj.Molecular_Weight=86/1000                   #Accoring Casal Example 2.9
subsObj.Boiling_Point=273+68.7                     #According Casal Example 2.9
subsObj.Liquid_Partial_Pressure_in_Atmosphere=0    #According Casal Example 2.9
subsObj.Lower_Flammability_Limit=0.03
subsObj.Upper_Flammability_Limit=3

#Define Outflow Models
tag=1
opr.OutFlowModel.TankHole(tag, Hole_Diameter=0.05, Hole_Height_FromBot=0, delta_t=100, Cd=1)

opr.Safety.Dike(tag=1, Height=10, Area=3.1415*11**2)

#Define Plant Units
xc=0
yc=0
D=5
#OnGroundTag=1
Uni=opr.PlantUnits.ONGStorage(1,SiteTag=SiteTAg,DikeTag=1,
                              Horizontal_localPosition=xc,Vertical_localPosition=yc,
                              Pressure=1.5*10**5 ,Temperature=2,
                              Diameter=5,Height=10,
                              SubstanceTag=1,SubstanceVolumeRatio=0.85) #Define a StorageTank


Uni.isdamaged=True

#These steps will be done Automatically By the Program inside the Analysis Part
OutFlowObj=opr.OutFlowModel.ObjManager[1]     # Get OutFlow Object
UnitObj=opr.PlantUnits.ObjManager[1]          # Get Unit Object
Subs=opr.Substance.ObjManager[1]              # Get Substance Object
SiteObj=opr.Sites.ObjManager[1]               # Get Site Object
UnitObj.OutFlowModelObject=deepcopy(OutFlowObj)  #Assign OutFlow Model to Unit Object
UnitObj.OutFlowModelObject.UnitObject=UnitObj
UnitObj.OutFlowModelObject.Calculate(); #Calculate OutFlow Calculations to get 


#Define Dispesion Spread Models and their connections to the materials and outflows
DispObject=opr.DispersionSpreadModels.LqdSprdGaussianGasDisp(tag=1,MatTags=[1], OutFlowModelTags=[1,2,3,4]) #Creat the Dispersion Object
UnitObj.DispersionSpreadModelObject=DispObject           #Assign Dispersion Object to the Unit Object
UnitObj.DispersionSpreadModelObject.UnitObject=UnitObj   #Assign the UnitObject to the Dispersion Model
UnitObj.DispersionSpreadModelname=DispObject.name

#Do Calculations
DispObject.Calculate();
poolArea=max(DispObject.LiquidRadious)**2*3.1415
V=Uni.V_subs
md=max(DispObject.LiquidVaporizationMassRate)
E=md/poolArea
h=V/poolArea 

print('The substance Height in Dike=',h)
print('Evaporation of mass per area (E)=',E)
print('Evaporation of mass md=',md)
print('Results are compatible with Casal Example 2.9 that md=0.851')

# t=DispObject.t_dispLiquidVaporization
# mt=DispObject.LiquidVaporizationMass
# plt.figure()
# plt.plot(t,mt)
# plt.title('Total vaporization vs time for Not boiling liquid');

### Plot Model

In [ ]:
#Plot the sampled plant unit
opr.Plot.Plotly.PlotUnits2D(GasConcentrationlist=[0.1,0.3],GasConcentrationHeght=0.5)

### Validate cross section of the plume Concentration values and longitudinal Concentration values

In [ ]:
#Plot cross section of the plume Concentration values and longitudinal Concentration values
x=[i/10 for i in range(-100,110)]
C=[DispObject.GasConcentration(4,X,0.5) for X in x]

plt.figure()
plt.plot(x,C,label='Code Results')
plt.ylabel('C')
plt.xlabel('y')
plt.title('Concentration at x=4 and z=0.5')

excelx=[-18,-17.5,-17,-16.5,-16,-15.5,-15,-14.5,-14,-13.5,-13,-12.5,-12,-11.5,-11,-10.5,-10,-9.5,-9,-8.5,-8,-7.5,-7,-6.5,-6,-5.5,-5,-4.5,-4,-3.5,-3,-2.5,-2,-1.5,-1,-0.5,0,0.5,1,1.5,2,2.5,3,3.5,4,4.5,5,5.5,6,6.5,7,7.5,8,8.5,9,9.5,10,10.5,11,11.5,12,12.5,13,13.5,14,14.5,15,15.5,16,16.5,17,17.5,18,18.5,19,19.5]
excelC=[2.75050362807037E-08,5.78984378520003E-08,1.193481540838E-07,2.40912204831127E-07,4.76207393888374E-07,9.21780893949689E-07,0.000001747243791382,3.24319861356762E-06,5.89505445753405E-06,1.04929193064724E-05,1.82893840944468E-05,3.12173521940422E-05,5.21779825972259E-05,0.000085402923762687,0.000136883918911059,0.000214845547446069,0.000330213269180967,0.00049700060795634,0.000732509995219599,0.00105721770152036,0.00149420275599164,0.00206799210319344,0.00280273769730309,0.00371972017028715,0.00483428578211008,0.00615245728422463,0.00766759436872633,0.00935758731811342,0.0111831173664259,0.013087482479099,0.0149983533024595,0.016831595361829,0.0184969967501868,0.0199054222426646,0.0209766341887419,0.0216468371878843,0.0218749632829608,0.0216468371878843,0.0209766341887419,0.0199054222426646,0.0184969967501868,0.016831595361829,0.0149983533024595,0.013087482479099,0.0111831173664259,0.00935758731811342,0.00766759436872633,0.00615245728422463,0.00483428578211008,0.00371972017028715,0.00280273769730309,0.00206799210319344,0.00149420275599164,0.00105721770152036,0.000732509995219599,0.00049700060795634,0.000330213269180967,0.000214845547446069,0.000136883918911059,0.000085402923762687,5.21779825972259E-05,3.12173521940422E-05,1.82893840944468E-05,1.04929193064724E-05,5.89505445753405E-06,3.24319861356762E-06,0.000001747243791382,9.21780893949689E-07,4.76207393888374E-07,2.40912204831127E-07,1.193481540838E-07,5.78984378520003E-08,2.75050362807037E-08,1.27953401015458E-08,5.8288876128192E-09,2.60024197941628E-09]
plt.plot(excelx,excelC,label='Excel Results')
plt.legend()

z=0.5
x=[i/100 for i in range(-100,170)]
C=[DispObject.GasConcentration(X,0,z) for X in x]





plt.figure()
plt.plot(x,C,label='Code Results')
plt.ylabel('C')
plt.xlabel('x')
plt.title('Concentration at y=0 and z=0.5')

excelx=[-1,-0.95,-0.9,-0.85,-0.8,-0.75,-0.7,-0.65,-0.6,-0.55,-0.5,-0.45,-0.4,-0.35,-0.3,-0.25,-0.2,-0.15,-0.0999999999999997,-0.0499999999999997,3.19189119579733E-16,0.0500000000000003,0.1,0.15,0.2,0.25,0.3,0.35,0.4,0.45,0.5,0.55,0.6,0.65,0.700000000000001,0.750000000000001,0.800000000000001,0.850000000000001,0.900000000000001,0.950000000000001,1,1.05,1.1,1.15,1.2,1.25,1.3,1.35,1.4,1.45,1.5,1.55,1.6,1.65,1.7,1.75,1.8,1.85,1.9,1.95,2,2.05,2.1,2.15,2.2,2.25,2.3,2.35,2.4,2.45,2.5,2.55,2.6,2.65,2.7,2.75]
excelC=[0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0.162423892233286,1.96268547574951,2.08831220306757,1.68587582341667,1.31309998590647,1.03310917766095,0.828613617339742,0.677733807163529,0.564234370189099,0.477076901346487,0.408835884324658,0.35445914467813,0.310446658467203,0.274326546239493,0.244320852205319,0.219129154922523,0.197785279752448,0.179560152695431,0.163894689817027,0.150352919493861,0.138589091386733,0.128324568560311,0.119331557667395,0.111421581353949,0.104437208531498,0.0982460081736155,0.0927360202223179,0.0878122702114609,0.0833940149263856,0.0794125140841289,0.0758091933134559,0.0725341086620575,0.0695446511868096,0.0668044479339553,0.0642824268059441,0.0619520200177139,0.0597904856694526,0.0577783303723033,0.0558988184257281,0.0541375550848942,0.0524821331548172,0.0509218336047612,0.0494473721664283,0.0480506849941132,0.0467247474438855,0.045463420886149,0.0442613232134041,0.0431137193534885,0.0420164286582596,0.0409657465184507,0.0399583779666248,0.0389913813804806,0.038062120696258,0.0371682247938889,0.0363075529283366]
plt.plot(excelx,excelC,label='Excel Results')
plt.legend()

### 3D show of dispered gas with desigred segment number

In [ ]:
from plotly.offline import plot
LFL=0.03
UFL=3

x,z,zt,yl,xpoints,ypoints,zpoints,Dx,Dy,Dz,Conc=DispObject._GasPoints(LFL,UFL,SegmentNumbers=10,errpercent=1)

# Plot 3D shape of the releases particles in the range of the LFL and UFL 
fig=go.Figure()
fig.update_layout(scene = dict(xaxis = dict(backgroundcolor="rgba(0, 0, 0,0)"),yaxis = dict(backgroundcolor="rgba(0, 0, 0,0)"),zaxis = dict(backgroundcolor="rgba(0, 0, 0,0)"),))
fig.update_layout(width=1000,height=800)


m=max(Conc)
color=[f'rgba(250,0,0,{int(i/m*900)/1000+0.1})' for i in Conc]
fig.add_scatter3d(x=xpoints,y=ypoints,z=zpoints,marker=dict(color=color,size=3),mode='markers',name='Code Results')

### Validate Center line of plume

In [ ]:
#Another Example to show the center line and dispersed gas and ...
#Calculate center line

LFL=0.03
UFL=3

x,z,zt,yl,xpoints,ypoints,zpoints,Dx,Dy,Dz,Conc=DispObject._GasPoints(LFL,UFL,SegmentNumbers=10,errpercent=1)

plt.figure()
plt.plot(x,z,label='Code Centerline')
plt.ylabel('z')
plt.xlabel('x')

plt.title('Center Line of Concentration plume')

excelX=[0.01,0.5,0.7,1,1.04,1.05,1.45,1.9,2,3]
excelC=[0.439062536,0.439062536,0.439062536,0.429062536,0.429062536,0.429062536,0.319062536,0.009062536,0.009062536,0.009062536]
plt.plot(excelX,excelC,label='Excel Centerline')
plt.legend()


### Validation of location of gas segments

In [ ]:
# Plot 3D shape of the releases particles in the range of the LFL and UFL 
fig=go.Figure()
fig.update_layout(scene = dict(xaxis = dict(backgroundcolor="rgba(0, 0, 0,0)"),yaxis = dict(backgroundcolor="rgba(0, 0, 0,0)"),zaxis = dict(backgroundcolor="rgba(0, 0, 0,0)"),))
fig.update_layout(width=1000,height=800)


m=max(Conc)
color=[f'rgba(250,0,0,{int(i/m*900)/1000+0.1})' for i in Conc]
fig.add_scatter3d(x=xpoints,y=ypoints,z=zpoints,marker=dict(color=color,size=3),mode='markers',name='Code Results')


excelConc=[0.030875701, 0.031118655, 0.03013374, 0.030052374, 0.038504674, 0.047399781, 0.056061852, 0.063706943, 0.069555955, 0.072964244, 0.073538383, 0.071210869, 0.066253179, 0.059223678, 0.050864203, 0.041971775, 0.033275965, 0.036865114, 0.051167454, 0.06823391, 0.087424855, 0.107621195, 0.127288426, 0.144646605, 0.157926784, 0.165665304, 0.166968887, 0.161684267, 0.150427832, 0.13446735, 0.115487165, 0.095296909, 0.075553072, 0.057551105, 0.042119521, 0.037024866, 0.055669238, 0.080420225, 0.111620382, 0.148850381, 0.190714897, 0.234772651, 0.277676171, 0.315542556, 0.3445129, 0.361394266, 0.364237996, 0.352709745, 0.328154142, 0.293336796, 0.251932048, 0.207887564, 0.164816932, 0.125546139, 0.091882566, 0.064608713, 0.043649301, 0.030444757, 0.049588143, 0.077601731, 0.116679133, 0.168555605, 0.233949124, 0.3119808, 0.399726125, 0.492068337, 0.581991347, 0.66135685, 0.722076822, 0.757459077, 0.763419352, 0.739256881, 0.687789921, 0.614815008, 0.528033326, 0.435718929, 0.345445661, 0.263136611, 0.192579934, 0.135415697, 0.09148612, 0.059384024, 0.037034993, 0.036164422, 0.061308211, 0.099858258, 0.156270697, 0.234962921, 0.339429306, 0.471115681, 0.628252182, 0.804949567, 0.990903946, 1.171986652, 1.331809147, 1.454084156, 1.525335268, 1.537337787, 1.488680546, 1.385038816, 1.238085386, 1.06332854, 0.877430172, 0.695642135, 0.529892063, 0.387808363, 0.272693727, 0.184230421, 0.11958474, 0.074579317, 0.04468783, 0.039655824, 0.069970646, 0.118618657, 0.193204992, 0.302351346, 0.454604458, 0.656725218, 0.911511009, 1.215537505, 1.557410252, 1.917193359, 2.26755079, 2.576774129, 2.813350878, 2.951206983, 2.974429366, 2.880287709, 2.679762485, 2.395438114, 2.057319908, 1.697645171, 1.345923069, 1.025231101, 0.750328648, 0.527605732, 0.356447607, 0.231371638, 0.144295491, 0.08646167, 0.04977631, 0.040141064, 0.073717324, 0.130070396, 0.220503548, 0.359154178, 0.562049396, 0.845076974, 1.220804924, 1.694433374, 2.259596754, 2.895113591, 2.501974136, 1.905830844, 1.394806965, 0.980781091, 0.662610451, 0.430103226, 0.268234934, 0.160726023, 0.092530579, 0.051181449, 0.037508286, 0.071693483, 0.131661973, 0.232310725, 0.393827811, 0.641463165, 1.003841822, 1.509339953, 2.180404511, 2.491178843, 1.75171272, 1.18344773, 0.768180891, 0.479077901, 0.287062854, 0.16526317, 0.091412036, 0.048580156, 0.032353555, 0.064364477, 0.123026509, 0.22593285, 0.398646798, 0.675811226, 1.100755193, 1.722599455, 2.590037717, 2.030804427, 1.31820368, 0.822100966, 0.492601827, 0.283592733, 0.15686368, 0.08336388, 0.042565885, 0.053341994, 0.106119082, 0.202836422, 0.372500295, 0.657257456, 1.114224343, 1.814838501, 2.840086362, 2.173350446, 1.35541535, 0.81216311, 0.467565372, 0.258624486, 0.137443803, 0.07017928, 0.034428719, 0.040808318, 0.084497665, 0.168100477, 0.3213079, 0.590068027, 1.041144438, 1.765013795, 2.874838456, 2.147078194, 1.286526454, 0.740658142, 0.40968032, 0.217721152, 0.111169171, 0.054537639, 0.06210869, 0.128602197, 0.255842463, 0.489018271, 0.898060853, 1.584581808, 2.686283141, 1.958043804, 1.127253218, 0.623517698, 0.331363224, 0.169195204, 0.083004189, 0.039123725, 0.04214213, 0.090820581, 0.188053011, 0.374114491, 0.715083882, 1.313220545, 2.317109558, 2.86321728, 1.648365009, 0.911760321, 0.484547336, 0.24741154, 0.121375747, 0.05721002, 0.059207483, 0.127598156, 0.264204625, 0.525611253, 1.004655377, 1.845006041, 2.315866448, 1.280975466, 0.680763612, 0.347600247, 0.170526563, 0.08037708, 0.036399937, 0.035630783, 0.079921743, 0.172239495, 0.35663894, 0.709500979, 1.356142909, 2.490497654, 1.729136015, 0.918934757, 0.469211255, 0.230186783, 0.108497709, 0.049134775, 0.046210635, 0.103652913, 0.223382583, 0.462535772, 0.920173166, 1.758822541, 2.242568521, 1.191794134, 0.608534193, 0.298536165, 0.140713943, 0.063724368, 0.057581997, 0.129159483, 0.278351839, 0.576355062, 1.14660637, 2.191627841, 2.794412451, 1.485066938, 0.758280298, 0.371998968, 0.17534037, 0.079405452, 0.034549912, 0.068938167, 0.154631976, 0.333247655, 0.690022288, 1.372737055, 2.623854905, 1.777947924, 0.907826339, 0.445363624, 0.209920536, 0.095065586, 0.041363755, 0.033966406, 0.079297767, 0.17786911, 0.383326046, 0.793714559, 1.579023467, 2.045126913, 1.044248852, 0.512290108, 0.241466092, 0.109351453, 0.047579644, 0.037538685, 0.087637586, 0.196575768, 0.423640798, 0.877190247, 1.745090814, 2.260214788, 1.154073462, 0.566168129, 0.266861303, 0.120852046, 0.052583638, 0.039859947, 0.093056791, 0.208731334, 0.449837282, 0.931432663, 1.853001204, 2.399978665, 1.22543738, 0.60117801, 0.283363084, 0.128325119, 0.055835229, 0.040665172, 0.094936663, 0.212947987, 0.458924598, 0.950248851, 1.890434311, 2.44846145, 1.250192857, 0.613322612, 0.289087398, 0.130917458, 0.056963175, 0.039859947, 0.093056791, 0.208731334, 0.449837282, 0.931432663, 1.853001204, 2.399978665, 1.22543738, 0.60117801, 0.283363084, 0.128325119, 0.055835229, 0.037538685, 0.087637586, 0.196575768, 0.423640798, 0.877190247, 1.745090814, 2.260214788, 1.154073462, 0.566168129, 0.266861303, 0.120852046, 0.052583638, 0.033966406, 0.079297767, 0.17786911, 0.383326046, 0.793714559, 1.579023467, 2.045126913, 1.044248852, 0.512290108, 0.241466092, 0.109351453, 0.047579644, 0.068938167, 0.154631976, 0.333247655, 0.690022288, 1.372737055, 2.623854905, 1.777947924, 0.907826339, 0.445363624, 0.209920536, 0.095065586, 0.041363755, 0.057581997, 0.129159483, 0.278351839, 0.576355062, 1.14660637, 2.191627841, 2.794412451, 1.485066938, 0.758280298, 0.371998968, 0.17534037, 0.079405452, 0.034549912, 0.046210635, 0.103652913, 0.223382583, 0.462535772, 0.920173166, 1.758822541, 2.242568521, 1.191794134, 0.608534193, 0.298536165, 0.140713943, 0.063724368, 0.035630783, 0.079921743, 0.172239495, 0.35663894, 0.709500979, 1.356142909, 2.490497654, 1.729136015, 0.918934757, 0.469211255, 0.230186783, 0.108497709, 0.049134775, 0.059207483, 0.127598156, 0.264204625, 0.525611253, 1.004655377, 1.845006041, 2.315866448, 1.280975466, 0.680763612, 0.347600247, 0.170526563, 0.08037708, 0.036399937, 0.04214213, 0.090820581, 0.188053011, 0.374114491, 0.715083882, 1.313220545, 2.317109558, 2.86321728, 1.648365009, 0.911760321, 0.484547336, 0.24741154, 0.121375747, 0.05721002, 0.06210869, 0.128602197, 0.255842463, 0.489018271, 0.898060853, 1.584581808, 2.686283141, 1.958043804, 1.127253218, 0.623517698, 0.331363224, 0.169195204, 0.083004189, 0.039123725, 0.040808318, 0.084497665, 0.168100477, 0.3213079, 0.590068027, 1.041144438, 1.765013795, 2.874838456, 2.147078194, 1.286526454, 0.740658142, 0.40968032, 0.217721152, 0.111169171, 0.054537639, 0.053341994, 0.106119082, 0.202836422, 0.372500295, 0.657257456, 1.114224343, 1.814838501, 2.840086362, 2.173350446, 1.35541535, 0.81216311, 0.467565372, 0.258624486, 0.137443803, 0.07017928, 0.034428719, 0.032353555, 0.064364477, 0.123026509, 0.22593285, 0.398646798, 0.675811226, 1.100755193, 1.722599455, 2.590037717, 2.030804427, 1.31820368, 0.822100966, 0.492601827, 0.283592733, 0.15686368, 0.08336388, 0.042565885, 0.037508286, 0.071693483, 0.131661973, 0.232310725, 0.393827811, 0.641463165, 1.003841822, 1.509339953, 2.180404511, 2.491178843, 1.75171272, 1.18344773, 0.768180891, 0.479077901, 0.287062854, 0.16526317, 0.091412036, 0.048580156, 0.040141064, 0.073717324, 0.130070396, 0.220503548, 0.359154178, 0.562049396, 0.845076974, 1.220804924, 1.694433374, 2.259596754, 2.895113591, 2.501974136, 1.905830844, 1.394806965, 0.980781091, 0.662610451, 0.430103226, 0.268234934, 0.160726023, 0.092530579, 0.051181449, 0.039655824, 0.069970646, 0.118618657, 0.193204992, 0.302351346, 0.454604458, 0.656725218, 0.911511009, 1.215537505, 1.557410252, 1.917193359, 2.26755079, 2.576774129, 2.813350878, 2.951206983, 2.974429366, 2.880287709, 2.679762485, 2.395438114, 2.057319908, 1.697645171, 1.345923069, 1.025231101, 0.750328648, 0.527605732, 0.356447607, 0.231371638, 0.144295491, 0.08646167, 0.04977631, 0.036164422, 0.061308211, 0.099858258, 0.156270697, 0.234962921, 0.339429306, 0.471115681, 0.628252182, 0.804949567, 0.990903946, 1.171986652, 1.331809147, 1.454084156, 1.525335268, 1.537337787, 1.488680546, 1.385038816, 1.238085386, 1.06332854, 0.877430172, 0.695642135, 0.529892063, 0.387808363, 0.272693727, 0.184230421, 0.11958474, 0.074579317, 0.04468783, 0.030444757, 0.049588143, 0.077601731, 0.116679133, 0.168555605, 0.233949124, 0.3119808, 0.399726125, 0.492068337, 0.581991347, 0.66135685, 0.722076822, 0.757459077, 0.763419352, 0.739256881, 0.687789921, 0.614815008, 0.528033326, 0.435718929, 0.345445661, 0.263136611, 0.192579934, 0.135415697, 0.09148612, 0.059384024, 0.037034993, 0.037024866, 0.055669238, 0.080420225, 0.111620382, 0.148850381, 0.190714897, 0.234772651, 0.277676171, 0.315542556, 0.3445129, 0.361394266, 0.364237996, 0.352709745, 0.328154142, 0.293336796, 0.251932048, 0.207887564, 0.164816932, 0.125546139, 0.091882566, 0.064608713, 0.043649301, 0.036865114, 0.051167454, 0.06823391, 0.087424855, 0.107621195, 0.127288426, 0.144646605, 0.157926784, 0.165665304, 0.166968887, 0.161684267, 0.150427832, 0.13446735, 0.115487165, 0.095296909, 0.075553072, 0.057551105, 0.042119521, 0.030052374, 0.038504674, 0.047399781, 0.056061852, 0.063706943, 0.069555955, 0.072964244, 0.073538383, 0.071210869, 0.066253179, 0.059223678, 0.050864203, 0.041971775, 0.033275965, 0.030875701, 0.031118655, 0.03013374, 0.030388449, 0.034702561, 0.038075248, 0.040137672, 0.040652742, 0.039559949, 0.036987061, 0.033225548, 0.031056551, 0.039987251, 0.049467289, 0.058795337, 0.067142249, 0.073667699, 0.077658061, 0.078654614, 0.076540286, 0.071562282, 0.064284535, 0.055482631, 0.04600826, 0.036655808, 0.030886151, 0.043079999, 0.057731893, 0.074333423, 0.091956131, 0.109296301, 0.12481261, 0.136942951, 0.144360747, 0.146213267, 0.142282884, 0.133029133, 0.119500324, 0.103138219, 0.085526045, 0.068140509, 0.05216036, 0.038362244, 0.03799889, 0.055163852, 0.076942533, 0.103111379, 0.13276235, 0.164237183, 0.195207395, 0.222920117, 0.244585373, 0.257833842, 0.261142513, 0.2541227, 0.237595145, 0.213432172, 0.184208822, 0.152752803, 0.121701568, 0.093160407, 0.068516442, 0.048415726, 0.032870501, 0.043155334, 0.065206357, 0.094661549, 0.132033915, 0.176939835, 0.227821104, 0.281832134, 0.334977229, 0.382532451, 0.419710178, 0.442444642, 0.448122345, 0.436076296, 0.407714899, 0.366251071, 0.316103603, 0.262124859, 0.208840726, 0.159863898, 0.117574685, 0.083081718, 0.056406004, 0.036793697, 0.045243323, 0.071151117, 0.107507107, 0.15607051, 0.217687125, 0.291724469, 0.3756135, 0.464662634, 0.552284082, 0.630689389, 0.691985098, 0.729467893, 0.738828842, 0.718968265, 0.672208226, 0.603845932, 0.521166734, 0.43217083, 0.344320147, 0.263571009, 0.193847884, 0.136978596, 0.092997779, 0.060662551, 0.038018675, 0.043785563, 0.07166877, 0.112708634, 0.170299212, 0.247227235, 0.344832511, 0.462113142, 0.594999574, 0.73605999, 0.874858847, 0.999058653, 1.096155592, 1.155531112, 1.170359548, 1.138898925, 1.064827563, 0.956536631, 0.825566666, 0.684590569, 0.545428587, 0.417515979, 0.30706939, 0.216984231, 0.147315363, 0.096093968, 0.060224394, 0.036264105, 0.039116846, 0.066639944, 0.109077113, 0.171538208, 0.259188853, 0.376270347, 0.524821825, 0.703318437, 0.905566478, 1.120255007, 1.331501532, 1.520528862, 1.668306671, 1.758673928, 1.781242239, 1.73336038, 1.620626614, 1.455811979, 1.256480727, 1.041920528, 0.830121341, 0.635443269, 0.467347807, 0.330241657, 0.224208319, 0.146251325, 0.091659212, 0.055192574, 0.031931065, 0.032259168, 0.057199962, 0.097446563, 0.159501782, 0.250837677, 0.379007866, 0.550214329, 0.767438867, 1.028451711, 1.324195905, 1.638131633, 1.947034171, 2.223445922, 2.439539135, 2.571681783, 2.604683076, 2.534666172, 2.369817323, 2.128811422, 1.837332404, 1.523584332, 1.213873644, 0.929198899, 0.683395496, 0.482907286, 0.327856369, 0.213861059, 0.134031853, 0.08070725, 0.046692304, 0.045322441, 0.080362948, 0.136907315, 0.224091644, 0.352413791, 0.532486188, 0.773022296, 1.078211388, 1.444920754, 1.860425847, 2.30148909, 2.735480967, 2.990868478, 2.581355733, 2.140556136, 1.705428851, 1.305475755, 0.960134855, 0.678459429, 0.460621016, 0.30046358, 0.188307729, 0.113389457, 0.065600239, 0.036464175, 0.033150287, 0.061178896, 0.108478634, 0.184805544, 0.30249208, 0.475708859, 0.718781171, 1.043470955, 1.455433138, 1.950439006, 2.511312215, 2.889448553, 2.302088155, 1.762207945, 1.296046491, 0.915824435, 0.621773336, 0.405583409, 0.254188846, 0.153059757, 0.088551061, 0.049221488, 0.042993604, 0.079344751, 0.140689204, 0.239679871, 0.392311079, 0.616961132, 0.932208926, 1.353308876, 1.887595026, 2.529583029, 2.98564739, 2.285460503, 1.680881688, 1.187760264, 0.806396546, 0.526013326, 0.329665162, 0.198507804, 0.114844535, 0.063836829, 0.034092629, 0.05357333, 0.098869648, 0.175309543, 0.29865951, 0.488849707, 0.76878091, 1.161603851, 1.6863267, 2.352088239, 2.847859152, 2.094507558, 1.480040427, 1.004831972, 0.655452966, 0.410788088, 0.247355955, 0.143105103, 0.079545587, 0.042482032, 0.033391468, 0.06413892, 0.118368459, 0.209883629, 0.357560351, 0.585259357, 0.920397854, 1.390692299, 2.018899605, 2.815960879, 2.507580816, 1.771930097, 1.203002284, 0.784719671, 0.491802631, 0.296138844, 0.171327914, 0.095233358, 0.050860226, 0.038409331, 0.07377732, 0.136156137, 0.241423639, 0.411292303, 0.673208503, 1.058709536, 1.599676914, 2.322287318, 2.884404511, 2.038204764, 1.383782007, 0.902642477, 0.565707681, 0.340640753, 0.19707401, 0.109544436, 0.058503186, 0.030019049, 0.042448876, 0.081536548, 0.150475803, 0.266814385, 0.454548292, 0.74401046, 1.17005499, 1.767916404, 2.566524407, 2.25256463, 1.529315631, 0.997574215, 0.625203677, 0.376466254, 0.217800465, 0.121065325, 0.06465602, 0.03317618, 0.045073768, 0.086578487, 0.159780707, 0.283313265, 0.482655989, 0.790017497, 1.24240715, 1.877238249, 2.725229413, 2.391855448, 1.623883229, 1.05926076, 0.663864113, 0.399745627, 0.231268494, 0.128551587, 0.068654125, 0.03522768, 0.045984318, 0.088327488, 0.163008492, 0.289036572, 0.492406286, 0.805976909, 1.267505439, 1.915160977, 2.780282699, 2.440174133, 1.656687846, 1.080659247, 0.677275058, 0.407821025, 0.235940427, 0.131148501, 0.07004103, 0.035939327, 0.045073768, 0.086578487, 0.159780707, 0.283313265, 0.482655989, 0.790017497, 1.24240715, 1.877238249, 2.725229413, 2.391855448, 1.623883229, 1.05926076, 0.663864113, 0.399745627, 0.231268494, 0.128551587, 0.068654125, 0.03522768, 0.042448876, 0.081536548, 0.150475803, 0.266814385, 0.454548292, 0.74401046, 1.17005499, 1.767916404, 2.566524407, 2.25256463, 1.529315631, 0.997574215, 0.625203677, 0.376466254, 0.217800465, 0.121065325, 0.06465602, 0.03317618, 0.038409331, 0.07377732, 0.136156137, 0.241423639, 0.411292303, 0.673208503, 1.058709536, 1.599676914, 2.322287318, 2.884404511, 2.038204764, 1.383782007, 0.902642477, 0.565707681, 0.340640753, 0.19707401, 0.109544436, 0.058503186, 0.030019049, 0.033391468, 0.06413892, 0.118368459, 0.209883629, 0.357560351, 0.585259357, 0.920397854, 1.390692299, 2.018899605, 2.815960879, 2.507580816, 1.771930097, 1.203002284, 0.784719671, 0.491802631, 0.296138844, 0.171327914, 0.095233358, 0.050860226, 0.05357333, 0.098869648, 0.175309543, 0.29865951, 0.488849707, 0.76878091, 1.161603851, 1.6863267, 2.352088239, 2.847859152, 2.094507558, 1.480040427, 1.004831972, 0.655452966, 0.410788088, 0.247355955, 0.143105103, 0.079545587, 0.042482032, 0.042993604, 0.079344751, 0.140689204, 0.239679871, 0.392311079, 0.616961132, 0.932208926, 1.353308876, 1.887595026, 2.529583029, 2.98564739, 2.285460503, 1.680881688, 1.187760264, 0.806396546, 0.526013326, 0.329665162, 0.198507804, 0.114844535, 0.063836829, 0.034092629, 0.033150287, 0.061178896, 0.108478634, 0.184805544, 0.30249208, 0.475708859, 0.718781171, 1.043470955, 1.455433138, 1.950439006, 2.511312215, 2.889448553, 2.302088155, 1.762207945, 1.296046491, 0.915824435, 0.621773336, 0.405583409, 0.254188846, 0.153059757, 0.088551061, 0.049221488, 0.045322441, 0.080362948, 0.136907315, 0.224091644, 0.352413791, 0.532486188, 0.773022296, 1.078211388, 1.444920754, 1.860425847, 2.30148909, 2.735480967, 2.990868478, 2.581355733, 2.140556136, 1.705428851, 1.305475755, 0.960134855, 0.678459429, 0.460621016, 0.30046358, 0.188307729, 0.113389457, 0.065600239, 0.036464175, 0.032259168, 0.057199962, 0.097446563, 0.159501782, 0.250837677, 0.379007866, 0.550214329, 0.767438867, 1.028451711, 1.324195905, 1.638131633, 1.947034171, 2.223445922, 2.439539135, 2.571681783, 2.604683076, 2.534666172, 2.369817323, 2.128811422, 1.837332404, 1.523584332, 1.213873644, 0.929198899, 0.683395496, 0.482907286, 0.327856369, 0.213861059, 0.134031853, 0.08070725, 0.046692304, 0.039116846, 0.066639944, 0.109077113, 0.171538208, 0.259188853, 0.376270347, 0.524821825, 0.703318437, 0.905566478, 1.120255007, 1.331501532, 1.520528862, 1.668306671, 1.758673928, 1.781242239, 1.73336038, 1.620626614, 1.455811979, 1.256480727, 1.041920528, 0.830121341, 0.635443269, 0.467347807, 0.330241657, 0.224208319, 0.146251325, 0.091659212, 0.055192574, 0.031931065, 0.043785563, 0.07166877, 0.112708634, 0.170299212, 0.247227235, 0.344832511, 0.462113142, 0.594999574, 0.73605999, 0.874858847, 0.999058653, 1.096155592, 1.155531112, 1.170359548, 1.138898925, 1.064827563, 0.956536631, 0.825566666, 0.684590569, 0.545428587, 0.417515979, 0.30706939, 0.216984231, 0.147315363, 0.096093968, 0.060224394, 0.036264105, 0.045243323, 0.071151117, 0.107507107, 0.15607051, 0.217687125, 0.291724469, 0.3756135, 0.464662634, 0.552284082, 0.630689389, 0.691985098, 0.729467893, 0.738828842, 0.718968265, 0.672208226, 0.603845932, 0.521166734, 0.43217083, 0.344320147, 0.263571009, 0.193847884, 0.136978596, 0.092997779, 0.060662551, 0.038018675, 0.043155334, 0.065206357, 0.094661549, 0.132033915, 0.176939835, 0.227821104, 0.281832134, 0.334977229, 0.382532451, 0.419710178, 0.442444642, 0.448122345, 0.436076296, 0.407714899, 0.366251071, 0.316103603, 0.262124859, 0.208840726, 0.159863898, 0.117574685, 0.083081718, 0.056406004, 0.036793697, 0.03799889, 0.055163852, 0.076942533, 0.103111379, 0.13276235, 0.164237183, 0.195207395, 0.222920117, 0.244585373, 0.257833842, 0.261142513, 0.2541227, 0.237595145, 0.213432172, 0.184208822, 0.152752803, 0.121701568, 0.093160407, 0.068516442, 0.048415726, 0.032870501, 0.030886151, 0.043079999, 0.057731893, 0.074333423, 0.091956131, 0.109296301, 0.12481261, 0.136942951, 0.144360747, 0.146213267, 0.142282884, 0.133029133, 0.119500324, 0.103138219, 0.085526045, 0.068140509, 0.05216036, 0.038362244, 0.031056551, 0.039987251, 0.049467289, 0.058795337, 0.067142249, 0.073667699, 0.077658061, 0.078654614, 0.076540286, 0.071562282, 0.064284535, 0.055482631, 0.04600826, 0.036655808, 0.030388449, 0.034702561, 0.038075248, 0.040137672, 0.040652742, 0.039559949, 0.036987061, 0.033225548, 0.0325101, 0.037295782, 0.041108283, 0.043533861, 0.044294852, 0.043301959, 0.040671487, 0.036702934, 0.031822899, 0.037595787, 0.046722292, 0.055787555, 0.063999817, 0.070542096, 0.074704404, 0.07601027, 0.074306459, 0.069792551, 0.062982487, 0.054608312, 0.045491046, 0.036410054, 0.035595996, 0.047921419, 0.061984973, 0.077032037, 0.091978128, 0.10551786, 0.116304254, 0.12316674, 0.125319749, 0.122510639, 0.115068464, 0.103840565, 0.090033886, 0.075002056, 0.06003003, 0.046162803, 0.034107038, 0.040241699, 0.056386691, 0.075911074, 0.098188783, 0.122024446, 0.14570016, 0.167148096, 0.184234543, 0.195105229, 0.198515754, 0.194065916, 0.18227696, 0.164491138, 0.142620337, 0.118808805, 0.095092009, 0.073125296, 0.054028072, 0.038353016, 0.041995998, 0.061246319, 0.085818376, 0.115533736, 0.149439553, 0.185716515, 0.221750042, 0.254392977, 0.280397892, 0.296942658, 0.302133345, 0.295360863, 0.277418525, 0.250349189, 0.217062669, 0.180822434, 0.144726382, 0.111293889, 0.082228648, 0.058371816, 0.03981177, 0.040457212, 0.061410101, 0.089559548, 0.125490889, 0.168943202, 0.218523156, 0.271570398, 0.324261669, 0.37199493, 0.410021516, 0.434214672, 0.441804935, 0.431901638, 0.405664834, 0.366081761, 0.317407396, 0.264413859, 0.211631157, 0.162743338, 0.120241685, 0.085356207, 0.058216137, 0.038148712, 0.035978283, 0.056840263, 0.086277974, 0.125826472, 0.176308123, 0.237356344, 0.307013582, 0.381542176, 0.455570651, 0.52263338, 0.576058741, 0.610048858, 0.620712779, 0.606799166, 0.569937831, 0.514325688, 0.445940757, 0.371487614, 0.297330685, 0.228645861, 0.168933266, 0.119920998, 0.081790622, 0.053596941, 0.033744634, 0.048565602, 0.076726329, 0.116463083, 0.169847971, 0.237991072, 0.320397552, 0.414424987, 0.515028067, 0.614956056, 0.705481271, 0.777597965, 0.823479824, 0.837874612, 0.819093199, 0.769335601, 0.69426706, 0.601957058, 0.501455828, 0.401354443, 0.308639629, 0.228036057, 0.161876415, 0.110405791, 0.072348303, 0.045550491, 0.038305217, 0.062986191, 0.099508685, 0.151044476, 0.220280944, 0.308657782, 0.415533225, 0.537480235, 0.667955396, 0.797555011, 0.914959886, 1.008490196, 1.067995759, 1.086664793, 1.062306614, 0.997774487, 0.900415838, 0.78069622, 0.65035315, 0.520528653, 0.400284021, 0.295746823, 0.209942393, 0.143188592, 0.093830691, 0.059075803, 0.035735723, 0.047731239, 0.078485627, 0.123995457, 0.188213007, 0.274486958, 0.38461128, 0.517786282, 0.669741614, 0.832323676, 0.99381474, 1.140110223, 1.256656167, 1.330804664, 1.354067712, 1.323715552, 1.243303571, 1.121987223, 0.972807393, 0.810389927, 0.648618642, 0.498784605, 0.368523234, 0.26160433, 0.178423972, 0.116920241, 0.073612983, 0.044529452, 0.033390008, 0.057144669, 0.093964355, 0.148449514, 0.22533188, 0.328620552, 0.460463302, 0.619902727, 0.801826289, 0.996472357, 1.189812263, 1.364959755, 1.504490582, 1.593262451, 1.621113376, 1.584775243, 1.488504623, 1.343262585, 1.164661902, 0.970212892, 0.776537501, 0.597153589, 0.441202415, 0.313197247, 0.213612278, 0.139978942, 0.088130741, 0.053311434, 0.030984288, 0.038407651, 0.065732015, 0.108084736, 0.170757586, 0.259193357, 0.378003611, 0.529658872, 0.713057865, 0.922319771, 1.146216043, 1.368609872, 1.570077443, 1.730576097, 1.832688052, 1.864724241, 1.822925439, 1.712187867, 1.545119756, 1.33968007, 1.116010469, 0.893230741, 0.686890127, 0.507503578, 0.360262587, 0.245712606, 0.16101411, 0.101374483, 0.061322745, 0.035640415, 0.042447019, 0.072645112, 0.119452107, 0.188716318, 0.286452961, 0.417758598, 0.585363582, 0.788050815, 1.019320988, 1.266764637, 1.512547828, 1.735203929, 1.912582374, 2.025433537, 2.060839002, 2.014644181, 1.892260237, 1.70762142, 1.480575453, 1.233382314, 0.987172638, 0.759130993, 0.560878195, 0.398151734, 0.271554427, 0.177948111, 0.11203613, 0.067772115, 0.03938875, 0.045071796, 0.077137234, 0.126838613, 0.200385883, 0.304166223, 0.443591347, 0.621560444, 0.836781156, 1.082352278, 1.345096987, 1.606078563, 1.842502948, 2.030849863, 2.150679352, 2.188274168, 2.13922282, 2.009271075, 1.813214831, 1.572129126, 1.309650417, 1.048215985, 0.806073032, 0.595560966, 0.422772062, 0.288346415, 0.188951808, 0.118964058, 0.071962908, 0.041824414, 0.045982307, 0.07869551, 0.129400923, 0.204433947, 0.310310788, 0.452552487, 0.634116798, 0.853685257, 1.104217244, 1.372269749, 1.638523502, 1.879723976, 2.071875752, 2.194125957, 2.232480239, 2.182437987, 2.049861043, 1.8498442, 1.603888241, 1.33610711, 1.069391352, 0.822356787, 0.607592095, 0.431312624, 0.294171399, 0.192768888, 0.121367291, 0.073416655, 0.042669323, 0.045071796, 0.077137234, 0.126838613, 0.200385883, 0.304166223, 0.443591347, 0.621560444, 0.836781156, 1.082352278, 1.345096987, 1.606078563, 1.842502948, 2.030849863, 2.150679352, 2.188274168, 2.13922282, 2.009271075, 1.813214831, 1.572129126, 1.309650417, 1.048215985, 0.806073032, 0.595560966, 0.422772062, 0.288346415, 0.188951808, 0.118964058, 0.071962908, 0.041824414, 0.042447019, 0.072645112, 0.119452107, 0.188716318, 0.286452961, 0.417758598, 0.585363582, 0.788050815, 1.019320988, 1.266764637, 1.512547828, 1.735203929, 1.912582374, 2.025433537, 2.060839002, 2.014644181, 1.892260237, 1.70762142, 1.480575453, 1.233382314, 0.987172638, 0.759130993, 0.560878195, 0.398151734, 0.271554427, 0.177948111, 0.11203613, 0.067772115, 0.03938875, 0.038407651, 0.065732015, 0.108084736, 0.170757586, 0.259193357, 0.378003611, 0.529658872, 0.713057865, 0.922319771, 1.146216043, 1.368609872, 1.570077443, 1.730576097, 1.832688052, 1.864724241, 1.822925439, 1.712187867, 1.545119756, 1.33968007, 1.116010469, 0.893230741, 0.686890127, 0.507503578, 0.360262587, 0.245712606, 0.16101411, 0.101374483, 0.061322745, 0.035640415, 0.033390008, 0.057144669, 0.093964355, 0.148449514, 0.22533188, 0.328620552, 0.460463302, 0.619902727, 0.801826289, 0.996472357, 1.189812263, 1.364959755, 1.504490582, 1.593262451, 1.621113376, 1.584775243, 1.488504623, 1.343262585, 1.164661902, 0.970212892, 0.776537501, 0.597153589, 0.441202415, 0.313197247, 0.213612278, 0.139978942, 0.088130741, 0.053311434, 0.030984288, 0.047731239, 0.078485627, 0.123995457, 0.188213007, 0.274486958, 0.38461128, 0.517786282, 0.669741614, 0.832323676, 0.99381474, 1.140110223, 1.256656167, 1.330804664, 1.354067712, 1.323715552, 1.243303571, 1.121987223, 0.972807393, 0.810389927, 0.648618642, 0.498784605, 0.368523234, 0.26160433, 0.178423972, 0.116920241, 0.073612983, 0.044529452, 0.038305217, 0.062986191, 0.099508685, 0.151044476, 0.220280944, 0.308657782, 0.415533225, 0.537480235, 0.667955396, 0.797555011, 0.914959886, 1.008490196, 1.067995759, 1.086664793, 1.062306614, 0.997774487, 0.900415838, 0.78069622, 0.65035315, 0.520528653, 0.400284021, 0.295746823, 0.209942393, 0.143188592, 0.093830691, 0.059075803, 0.035735723, 0.048565602, 0.076726329, 0.116463083, 0.169847971, 0.237991072, 0.320397552, 0.414424987, 0.515028067, 0.614956056, 0.705481271, 0.777597965, 0.823479824, 0.837874612, 0.819093199, 0.769335601, 0.69426706, 0.601957058, 0.501455828, 0.401354443, 0.308639629, 0.228036057, 0.161876415, 0.110405791, 0.072348303, 0.045550491, 0.035978283, 0.056840263, 0.086277974, 0.125826472, 0.176308123, 0.237356344, 0.307013582, 0.381542176, 0.455570651, 0.52263338, 0.576058741, 0.610048858, 0.620712779, 0.606799166, 0.569937831, 0.514325688, 0.445940757, 0.371487614, 0.297330685, 0.228645861, 0.168933266, 0.119920998, 0.081790622, 0.053596941, 0.033744634, 0.040457212, 0.061410101, 0.089559548, 0.125490889, 0.168943202, 0.218523156, 0.271570398, 0.324261669, 0.37199493, 0.410021516, 0.434214672, 0.441804935, 0.431901638, 0.405664834, 0.366081761, 0.317407396, 0.264413859, 0.211631157, 0.162743338, 0.120241685, 0.085356207, 0.058216137, 0.038148712, 0.041995998, 0.061246319, 0.085818376, 0.115533736, 0.149439553, 0.185716515, 0.221750042, 0.254392977, 0.280397892, 0.296942658, 0.302133345, 0.295360863, 0.277418525, 0.250349189, 0.217062669, 0.180822434, 0.144726382, 0.111293889, 0.082228648, 0.058371816, 0.03981177, 0.040241699, 0.056386691, 0.075911074, 0.098188783, 0.122024446, 0.14570016, 0.167148096, 0.184234543, 0.195105229, 0.198515754, 0.194065916, 0.18227696, 0.164491138, 0.142620337, 0.118808805, 0.095092009, 0.073125296, 0.054028072, 0.038353016, 0.035595996, 0.047921419, 0.061984973, 0.077032037, 0.091978128, 0.10551786, 0.116304254, 0.12316674, 0.125319749, 0.122510639, 0.115068464, 0.103840565, 0.090033886, 0.075002056, 0.06003003, 0.046162803, 0.034107038, 0.037595787, 0.046722292, 0.055787555, 0.063999817, 0.070542096, 0.074704404, 0.07601027, 0.074306459, 0.069792551, 0.062982487, 0.054608312, 0.045491046, 0.036410054, 0.0325101, 0.037295782, 0.041108283, 0.043533861, 0.044294852, 0.043301959, 0.040671487, 0.036702934, 0.031822899, 0.032565209, 0.035885405, 0.037993566, 0.038648307, 0.037772795, 0.035469576, 0.032000818, 0.030325421, 0.037677845, 0.04497732, 0.0515857, 0.056845136, 0.060184619, 0.061221778, 0.059834902, 0.056186432, 0.050691663, 0.043940991, 0.036595811, 0.035691093, 0.046154125, 0.057344232, 0.068453751, 0.078511452, 0.086516112, 0.091598676, 0.093177193, 0.091066421, 0.085513589, 0.077150763, 0.066876499, 0.055697418, 0.044568171, 0.034264373, 0.03877667, 0.052190535, 0.067490466, 0.083853586, 0.100098866, 0.114806087, 0.126511177, 0.133943333, 0.136251573, 0.133165024, 0.125045204, 0.112816371, 0.097792475, 0.081445476, 0.06517135, 0.050104264, 0.037010153, 0.038890393, 0.054479189, 0.073324967, 0.094820568, 0.117809894, 0.14063366, 0.161296535, 0.177741573, 0.188183362, 0.19142632, 0.18708988, 0.175681958, 0.158501089, 0.137393302, 0.114426625, 0.091562331, 0.070393865, 0.051997325, 0.036902468, 0.036007159, 0.05249654, 0.073539213, 0.098978352, 0.127994379, 0.159026723, 0.189835585, 0.217727548, 0.239926028, 0.254020969, 0.258398503, 0.252544922, 0.237145838, 0.213954091, 0.185461558, 0.154459788, 0.123596219, 0.095021778, 0.070189047, 0.049813122, 0.033966155, 0.030779571, 0.046698768, 0.068084342, 0.095375218, 0.128368003, 0.165999761, 0.206246542, 0.246203482, 0.282377408, 0.311167284, 0.329447437, 0.335124793, 0.327533108, 0.307561573, 0.277483498, 0.240530675, 0.200323546, 0.160295654, 0.123236603, 0.091030287, 0.064604136, 0.044051729, 0.038353707, 0.058190248, 0.084838314, 0.11884484, 0.159956382, 0.20684844, 0.256999017, 0.30678843, 0.351863917, 0.387738312, 0.410516786, 0.417591207, 0.408131384, 0.383245319, 0.34576573, 0.299719677, 0.249618509, 0.199740685, 0.153562264, 0.113430722, 0.080501711, 0.054891834, 0.035961566, 0.045917724, 0.069666376, 0.101569902, 0.142283106, 0.191502557, 0.247642544, 0.307683685, 0.367292435, 0.421257591, 0.464207039, 0.491477824, 0.499947444, 0.488621979, 0.45882795, 0.413956736, 0.358829601, 0.298847613, 0.239133016, 0.183847409, 0.13580123, 0.096378046, 0.065717457, 0.043053811, 0.033468848, 0.052817955, 0.080135406, 0.116833197, 0.163664529, 0.220280374, 0.284856729, 0.353920482, 0.422486864, 0.484561569, 0.533965195, 0.565334063, 0.575076445, 0.56204906, 0.527777769, 0.476163587, 0.412752288, 0.343756579, 0.275068443, 0.211474857, 0.156208597, 0.110861141, 0.075593069, 0.049523671, 0.031172519, 0.036988797, 0.058372868, 0.088563321, 0.129120652, 0.180877278, 0.243447463, 0.314815373, 0.391142624, 0.466920196, 0.535523354, 0.590122804, 0.624790766, 0.635557763, 0.621160276, 0.583284642, 0.526242149, 0.456161825, 0.379909774, 0.303997644, 0.233715862, 0.172637198, 0.122520509, 0.083543261, 0.054732121, 0.034450962, 0.039276057, 0.061982445, 0.094039771, 0.137105027, 0.192062104, 0.258501414, 0.334282468, 0.415329533, 0.495792928, 0.568638269, 0.626613961, 0.663425669, 0.67485846, 0.659570682, 0.61935295, 0.558783146, 0.484369297, 0.403402083, 0.322795808, 0.248168044, 0.183312487, 0.130096754, 0.088709288, 0.058116566, 0.03658129, 0.040069486, 0.063234573, 0.0959395, 0.139874733, 0.195942016, 0.263723489, 0.341035422, 0.423719746, 0.50580861, 0.580125524, 0.639272402, 0.676827757, 0.688491505, 0.672894894, 0.631864709, 0.570071314, 0.494154206, 0.411551345, 0.329316716, 0.253181371, 0.187015644, 0.132724883, 0.090501335, 0.059290599, 0.037320282, 0.039276057, 0.061982445, 0.094039771, 0.137105027, 0.192062104, 0.258501414, 0.334282468, 0.415329533, 0.495792928, 0.568638269, 0.626613961, 0.663425669, 0.67485846, 0.659570682, 0.61935295, 0.558783146, 0.484369297, 0.403402083, 0.322795808, 0.248168044, 0.183312487, 0.130096754, 0.088709288, 0.058116566, 0.03658129, 0.036988797, 0.058372868, 0.088563321, 0.129120652, 0.180877278, 0.243447463, 0.314815373, 0.391142624, 0.466920196, 0.535523354, 0.590122804, 0.624790766, 0.635557763, 0.621160276, 0.583284642, 0.526242149, 0.456161825, 0.379909774, 0.303997644, 0.233715862, 0.172637198, 0.122520509, 0.083543261, 0.054732121, 0.034450962, 0.033468848, 0.052817955, 0.080135406, 0.116833197, 0.163664529, 0.220280374, 0.284856729, 0.353920482, 0.422486864, 0.484561569, 0.533965195, 0.565334063, 0.575076445, 0.56204906, 0.527777769, 0.476163587, 0.412752288, 0.343756579, 0.275068443, 0.211474857, 0.156208597, 0.110861141, 0.075593069, 0.049523671, 0.031172519, 0.045917724, 0.069666376, 0.101569902, 0.142283106, 0.191502557, 0.247642544, 0.307683685, 0.367292435, 0.421257591, 0.464207039, 0.491477824, 0.499947444, 0.488621979, 0.45882795, 0.413956736, 0.358829601, 0.298847613, 0.239133016, 0.183847409, 0.13580123, 0.096378046, 0.065717457, 0.043053811, 0.038353707, 0.058190248, 0.084838314, 0.11884484, 0.159956382, 0.20684844, 0.256999017, 0.30678843, 0.351863917, 0.387738312, 0.410516786, 0.417591207, 0.408131384, 0.383245319, 0.34576573, 0.299719677, 0.249618509, 0.199740685, 0.153562264, 0.113430722, 0.080501711, 0.054891834, 0.035961566, 0.030779571, 0.046698768, 0.068084342, 0.095375218, 0.128368003, 0.165999761, 0.206246542, 0.246203482, 0.282377408, 0.311167284, 0.329447437, 0.335124793, 0.327533108, 0.307561573, 0.277483498, 0.240530675, 0.200323546, 0.160295654, 0.123236603, 0.091030287, 0.064604136, 0.044051729, 0.036007159, 0.05249654, 0.073539213, 0.098978352, 0.127994379, 0.159026723, 0.189835585, 0.217727548, 0.239926028, 0.254020969, 0.258398503, 0.252544922, 0.237145838, 0.213954091, 0.185461558, 0.154459788, 0.123596219, 0.095021778, 0.070189047, 0.049813122, 0.033966155, 0.038890393, 0.054479189, 0.073324967, 0.094820568, 0.117809894, 0.14063366, 0.161296535, 0.177741573, 0.188183362, 0.19142632, 0.18708988, 0.175681958, 0.158501089, 0.137393302, 0.114426625, 0.091562331, 0.070393865, 0.051997325, 0.036902468, 0.03877667, 0.052190535, 0.067490466, 0.083853586, 0.100098866, 0.114806087, 0.126511177, 0.133943333, 0.136251573, 0.133165024, 0.125045204, 0.112816371, 0.097792475, 0.081445476, 0.06517135, 0.050104264, 0.037010153, 0.035691093, 0.046154125, 0.057344232, 0.068453751, 0.078511452, 0.086516112, 0.091598676, 0.093177193, 0.091066421, 0.085513589, 0.077150763, 0.066876499, 0.055697418, 0.044568171, 0.034264373, 0.030325421, 0.037677845, 0.04497732, 0.0515857, 0.056845136, 0.060184619, 0.061221778, 0.059834902, 0.056186432, 0.050691663, 0.043940991, 0.036595811, 0.032565209, 0.035885405, 0.037993566, 0.038648307, 0.037772795, 0.035469576, 0.032000818, 0.033136932, 0.036279816, 0.038176156, 0.038601951, 0.03750426, 0.035009924, 0.031400358, 0.035977478, 0.042556441, 0.048455625, 0.053051416, 0.055824404, 0.056447038, 0.054841901, 0.051194473, 0.04591626, 0.039567638, 0.032759917, 0.032659104, 0.041238482, 0.050546471, 0.059789569, 0.068077614, 0.074534459, 0.078430362, 0.07930513, 0.077049997, 0.071925551, 0.064509939, 0.055590458, 0.046025966, 0.036612902, 0.034336171, 0.044085179, 0.055666128, 0.068230599, 0.080707477, 0.091895167, 0.100610996, 0.105869915, 0.107050729, 0.104006617, 0.097089338, 0.087079309, 0.075039269, 0.062128556, 0.049422248, 0.037773054, 0.035039111, 0.044531613, 0.057175394, 0.072195076, 0.088490317, 0.104671955, 0.119181607, 0.130485427, 0.137305879, 0.138837311, 0.134889311, 0.125918084, 0.112935776, 0.097320685, 0.080576393, 0.0640972, 0.04898901, 0.035973819, 0.033893493, 0.036359018, 0.04366142, 0.055489807, 0.071244929, 0.089960605, 0.110265725, 0.130429287, 0.148509427, 0.162594855, 0.17109366, 0.173001942, 0.168082432, 0.156903594, 0.140726643, 0.121269041, 0.100404369, 0.07987003, 0.061044065, 0.044826139, 0.031626233, 0.040577878, 0.043529648, 0.052272211, 0.06643336, 0.085295666, 0.107702398, 0.132012041, 0.156152208, 0.177798065, 0.194661383, 0.204836301, 0.207120929, 0.201231206, 0.187847708, 0.16848038, 0.145185402, 0.120205854, 0.095621786, 0.073083015, 0.053666632, 0.037863476, 0.04667567, 0.050071013, 0.060127354, 0.076416554, 0.098113369, 0.123887246, 0.151849991, 0.179617793, 0.204516455, 0.223913889, 0.23561783, 0.238245778, 0.231470984, 0.216076296, 0.193798567, 0.167002964, 0.138269644, 0.109991235, 0.084065477, 0.061731321, 0.043553364, 0.051584593, 0.055337027, 0.066451003, 0.084453353, 0.108432042, 0.136916582, 0.167820194, 0.198508361, 0.226025639, 0.247463118, 0.260397973, 0.263302305, 0.255815, 0.238801239, 0.21418054, 0.184566819, 0.152811589, 0.121559115, 0.092906721, 0.068223661, 0.048133911, 0.032628381, 0.054774406, 0.058758878, 0.070560104, 0.089675656, 0.115137105, 0.14538303, 0.178197616, 0.210783433, 0.240002284, 0.262765383, 0.276500085, 0.27958401, 0.271633716, 0.253567883, 0.227424725, 0.195979794, 0.16226093, 0.12907591, 0.098651752, 0.072442376, 0.051110346, 0.034646007, 0.055880923, 0.059945886, 0.071985513, 0.091487225, 0.117463029, 0.148319962, 0.181797446, 0.215041541, 0.244850651, 0.268073596, 0.282085757, 0.285231982, 0.277121081, 0.258690294, 0.23201901, 0.199938848, 0.165538818, 0.131683417, 0.100644649, 0.073905809, 0.052142844, 0.035345903, 0.054774406, 0.058758878, 0.070560104, 0.089675656, 0.115137105, 0.14538303, 0.178197616, 0.210783433, 0.240002284, 0.262765383, 0.276500085, 0.27958401, 0.271633716, 0.253567883, 0.227424725, 0.195979794, 0.16226093, 0.12907591, 0.098651752, 0.072442376, 0.051110346, 0.034646007, 0.051584593, 0.055337027, 0.066451003, 0.084453353, 0.108432042, 0.136916582, 0.167820194, 0.198508361, 0.226025639, 0.247463118, 0.260397973, 0.263302305, 0.255815, 0.238801239, 0.21418054, 0.184566819, 0.152811589, 0.121559115, 0.092906721, 0.068223661, 0.048133911, 0.032628381, 0.04667567, 0.050071013, 0.060127354, 0.076416554, 0.098113369, 0.123887246, 0.151849991, 0.179617793, 0.204516455, 0.223913889, 0.23561783, 0.238245778, 0.231470984, 0.216076296, 0.193798567, 0.167002964, 0.138269644, 0.109991235, 0.084065477, 0.061731321, 0.043553364, 0.040577878, 0.043529648, 0.052272211, 0.06643336, 0.085295666, 0.107702398, 0.132012041, 0.156152208, 0.177798065, 0.194661383, 0.204836301, 0.207120929, 0.201231206, 0.187847708, 0.16848038, 0.145185402, 0.120205854, 0.095621786, 0.073083015, 0.053666632, 0.037863476, 0.033893493, 0.036359018, 0.04366142, 0.055489807, 0.071244929, 0.089960605, 0.110265725, 0.130429287, 0.148509427, 0.162594855, 0.17109366, 0.173001942, 0.168082432, 0.156903594, 0.140726643, 0.121269041, 0.100404369, 0.07987003, 0.061044065, 0.044826139, 0.031626233, 0.035039111, 0.044531613, 0.057175394, 0.072195076, 0.088490317, 0.104671955, 0.119181607, 0.130485427, 0.137305879, 0.138837311, 0.134889311, 0.125918084, 0.112935776, 0.097320685, 0.080576393, 0.0640972, 0.04898901, 0.035973819, 0.034336171, 0.044085179, 0.055666128, 0.068230599, 0.080707477, 0.091895167, 0.100610996, 0.105869915, 0.107050729, 0.104006617, 0.097089338, 0.087079309, 0.075039269, 0.062128556, 0.049422248, 0.037773054, 0.032659104, 0.041238482, 0.050546471, 0.059789569, 0.068077614, 0.074534459, 0.078430362, 0.07930513, 0.077049997, 0.071925551, 0.064509939, 0.055590458, 0.046025966, 0.036612902, 0.035977478, 0.042556441, 0.048455625, 0.053051416, 0.055824404, 0.056447038, 0.054841901, 0.051194473, 0.04591626, 0.039567638, 0.032759917, 0.033136932, 0.036279816, 0.038176156, 0.038601951, 0.03750426, 0.035009924, 0.031400358, 0.030419515, 0.033438452, 0.036314773, 0.038526179, 0.039645649, 0.039408671, 0.03774949, 0.034799581, 0.030850271, 0.03425626, 0.035106906, 0.037513348, 0.041062051, 0.04513719, 0.049019816, 0.052004902, 0.053516028, 0.053196141, 0.050956482, 0.046974521, 0.04164351, 0.035487623, 0.044427974, 0.045531202, 0.04865219, 0.053254609, 0.058539779, 0.063575274, 0.067446722, 0.069406547, 0.068991676, 0.066086995, 0.060922669, 0.054008722, 0.046024966, 0.03769381, 0.055360664, 0.056735371, 0.060624361, 0.066359329, 0.072945057, 0.079219669, 0.08404379, 0.086485884, 0.085968922, 0.082349466, 0.07591432, 0.067299011, 0.05735064, 0.04696938, 0.036964492, 0.066278748, 0.067924572, 0.072580538, 0.079446541, 0.087331088, 0.094843163, 0.100618685, 0.103542401, 0.102923486, 0.098590211, 0.090885942, 0.080571545, 0.068661181, 0.056232557, 0.044254532, 0.03346506, 0.076238708, 0.078131855, 0.083487491, 0.091385275, 0.100454663, 0.109095606, 0.115739037, 0.119102111, 0.11839019, 0.113405736, 0.104543718, 0.092679337, 0.078979158, 0.064682837, 0.050904829, 0.038493982, 0.084256803, 0.086349054, 0.092267947, 0.100996348, 0.111019572, 0.120569291, 0.127911418, 0.13162819, 0.130841395, 0.125332722, 0.115538677, 0.102426508, 0.087285469, 0.07148559, 0.056258536, 0.04254243, 0.089466952, 0.091688581, 0.097973479, 0.107241613, 0.117884639, 0.128024879, 0.135821018, 0.139767623, 0.138932175, 0.133082865, 0.12268319, 0.10876021, 0.092682901, 0.075906012, 0.05973737, 0.045173106, 0.091274305, 0.093540814, 0.099952674, 0.109408037, 0.120266066, 0.130611154, 0.138564785, 0.142591116, 0.141738791, 0.135771317, 0.125161555, 0.110957311, 0.094555219, 0.077439416, 0.060944145, 0.046085664, 0.089466952, 0.091688581, 0.097973479, 0.107241613, 0.117884639, 0.128024879, 0.135821018, 0.139767623, 0.138932175, 0.133082865, 0.12268319, 0.10876021, 0.092682901, 0.075906012, 0.05973737, 0.045173106, 0.084256803, 0.086349054, 0.092267947, 0.100996348, 0.111019572, 0.120569291, 0.127911418, 0.13162819, 0.130841395, 0.125332722, 0.115538677, 0.102426508, 0.087285469, 0.07148559, 0.056258536, 0.04254243, 0.076238708, 0.078131855, 0.083487491, 0.091385275, 0.100454663, 0.109095606, 0.115739037, 0.119102111, 0.11839019, 0.113405736, 0.104543718, 0.092679337, 0.078979158, 0.064682837, 0.050904829, 0.038493982, 0.066278748, 0.067924572, 0.072580538, 0.079446541, 0.087331088, 0.094843163, 0.100618685, 0.103542401, 0.102923486, 0.098590211, 0.090885942, 0.080571545, 0.068661181, 0.056232557, 0.044254532, 0.03346506, 0.055360664, 0.056735371, 0.060624361, 0.066359329, 0.072945057, 0.079219669, 0.08404379, 0.086485884, 0.085968922, 0.082349466, 0.07591432, 0.067299011, 0.05735064, 0.04696938, 0.036964492, 0.044427974, 0.045531202, 0.04865219, 0.053254609, 0.058539779, 0.063575274, 0.067446722, 0.069406547, 0.068991676, 0.066086995, 0.060922669, 0.054008722, 0.046024966, 0.03769381, 0.03425626, 0.035106906, 0.037513348, 0.041062051, 0.04513719, 0.049019816, 0.052004902, 0.053516028, 0.053196141, 0.050956482, 0.046974521, 0.04164351, 0.035487623, 0.030419515, 0.033438452, 0.036314773, 0.038526179, 0.039645649, 0.039408671, 0.03774949, 0.034799581, 0.030850271, 0.031754749, 0.031900593, 0.032267715, 0.032663431, 0.032823152, 0.032478494, 0.031424524, 0.041183689, 0.041372838, 0.041848971, 0.042362186, 0.042569333, 0.042122336, 0.04075541, 0.038348567, 0.034952816, 0.03077414, 0.051318036, 0.051553731, 0.052147029, 0.052786534, 0.053044655, 0.052487662, 0.050784369, 0.047785257, 0.043553891, 0.038346939, 0.0325533, 0.061438844, 0.061721022, 0.062431328, 0.063196955, 0.063505982, 0.062839141, 0.060799928, 0.057209339, 0.052143475, 0.045909622, 0.038973375, 0.031860719, 0.070671493, 0.070996074, 0.071813121, 0.072693802, 0.073049267, 0.072282217, 0.069936564, 0.065806404, 0.059979273, 0.052808635, 0.044830053, 0.03664855, 0.078104078, 0.078462797, 0.079365773, 0.080339076, 0.080731926, 0.079884204, 0.077291857, 0.072727324, 0.066287348, 0.058362568, 0.04954487, 0.040502911, 0.031859945, 0.082933765, 0.083314665, 0.084273478, 0.085306967, 0.085724109, 0.084823968, 0.082071318, 0.07722453, 0.070386329, 0.061971507, 0.052608554, 0.043007472, 0.033830054, 0.084609138, 0.084997733, 0.085975915, 0.087030282, 0.087455851, 0.086537526, 0.083729269, 0.078784569, 0.071808227, 0.063223415, 0.053671317, 0.04387628, 0.034513467, 0.082933765, 0.083314665, 0.084273478, 0.085306967, 0.085724109, 0.084823968, 0.082071318, 0.07722453, 0.070386329, 0.061971507, 0.052608554, 0.043007472, 0.033830054, 0.078104078, 0.078462797, 0.079365773, 0.080339076, 0.080731926, 0.079884204, 0.077291857, 0.072727324, 0.066287348, 0.058362568, 0.04954487, 0.040502911, 0.031859945, 0.070671493, 0.070996074, 0.071813121, 0.072693802, 0.073049267, 0.072282217, 0.069936564, 0.065806404, 0.059979273, 0.052808635, 0.044830053, 0.03664855, 0.061438844, 0.061721022, 0.062431328, 0.063196955, 0.063505982, 0.062839141, 0.060799928, 0.057209339, 0.052143475, 0.045909622, 0.038973375, 0.031860719, 0.051318036, 0.051553731, 0.052147029, 0.052786534, 0.053044655, 0.052487662, 0.050784369, 0.047785257, 0.043553891, 0.038346939, 0.0325533, 0.041183689, 0.041372838, 0.041848971, 0.042362186, 0.042569333, 0.042122336, 0.04075541, 0.038348567, 0.034952816, 0.03077414, 0.031754749, 0.031900593, 0.032267715, 0.032663431, 0.032823152, 0.032478494, 0.031424524, 0.031982064, 0.031814275, 0.031289744, 0.030354739, 0.039852106, 0.039643028, 0.038989422, 0.037824334, 0.036072183, 0.033688738, 0.030694695, 0.047711633, 0.047461321, 0.046678812, 0.045283949, 0.043186244, 0.040332743, 0.036748221, 0.032553804, 0.054881441, 0.054593514, 0.053693415, 0.05208894, 0.049676005, 0.046393697, 0.042270516, 0.037445788, 0.03215958, 0.060653373, 0.060335164, 0.059340401, 0.057567182, 0.054900476, 0.051272965, 0.046716145, 0.041383996, 0.035541832, 0.064403968, 0.064066082, 0.063009806, 0.061126938, 0.058295332, 0.054443508, 0.04960491, 0.043943039, 0.037739617, 0.031350793, 0.065705015, 0.065360303, 0.064282689, 0.062361784, 0.059472976, 0.05554334, 0.050606996, 0.044830747, 0.038502007, 0.031984121, 0.064403968, 0.064066082, 0.063009806, 0.061126938, 0.058295332, 0.054443508, 0.04960491, 0.043943039, 0.037739617, 0.031350793, 0.060653373, 0.060335164, 0.059340401, 0.057567182, 0.054900476, 0.051272965, 0.046716145, 0.041383996, 0.035541832, 0.054881441, 0.054593514, 0.053693415, 0.05208894, 0.049676005, 0.046393697, 0.042270516, 0.037445788, 0.03215958, 0.047711633, 0.047461321, 0.046678812, 0.045283949, 0.043186244, 0.040332743, 0.036748221, 0.032553804, 0.039852106, 0.039643028, 0.038989422, 0.037824334, 0.036072183, 0.033688738, 0.030694695, 0.031982064, 0.031814275, 0.031289744, 0.030354739, 0.035167948, 0.034797565, 0.033697932, 0.031906464, 0.040452769, 0.040026727, 0.038761848, 0.03670117, 0.03392524, 0.030558912, 0.044707224, 0.044236374, 0.042838467, 0.040561065, 0.037493189, 0.033772821, 0.047471765, 0.046971799, 0.04548745, 0.043069221, 0.039811638, 0.035861215, 0.031416376, 0.048430758, 0.047920692, 0.046406358, 0.043939277, 0.040615886, 0.03658566, 0.032051029, 0.047471765, 0.046971799, 0.04548745, 0.043069221, 0.039811638, 0.035861215, 0.031416376, 0.044707224, 0.044236374, 0.042838467, 0.040561065, 0.037493189, 0.033772821, 0.040452769, 0.040026727, 0.038761848, 0.03670117, 0.03392524, 0.030558912, 0.035167948, 0.034797565, 0.033697932, 0.031906464, 0.032705853, 0.032261302, 0.030958701, 0.03472827, 0.03425623, 0.032873081, 0.030675182, 0.035429828, 0.034948252, 0.033537161, 0.031294862, 0.03472827, 0.03425623, 0.032873081, 0.030675182, 0.032705853, 0.032261302, 0.030958701]
m=max(excelConc)
color=[f'rgba(0,0,250,{int(i/m*900)/1000+0.1})' for i in excelConc]
fig.add_scatter3d(x=xpoints,y=ypoints,z=zpoints,marker=dict(color=color,size=3),mode='markers',name='Excel Results')
fig.show()

print(min([i-j for i,j in zip(Conc, excelConc)]))

### Calculate the Mass and Center mass of the released Gass

In [ ]:
#Calculate the Mass and Center mass of the released Gass
print(DispObject._MassCMass(Dx,Dy,Dz,xpoints,zpoints,Concentrations=Conc))

### Get the calculated gas center and location

In [ ]:
# Usage of Give Boundary
points=DispObject.GiveBoundary(C=0.03,z=0.5,SegmentNumbers=10,errpercent=1)
print(DispObject.GasExplosiveCenterX)
print(DispObject.GasExplosiveCenterY)
print(DispObject.GasExplosiveCenterZ)
print(DispObject.GasExplosiveMass)
# print(points)

In [ ]:
# Plot of the Given Boundary
import plotly.graph_objects as go

fig=go.Figure()

fig.add_scatter(x=[p[0] for p in points], y=[p[1] for p in points],mode='lines',line=dict(color=f'rgba(250, 250, 5,1)'),fill='toself') #'['none', 'tozeroy', 'tozerox', 'tonexty', 'tonextx',  'toself', 'tonext']'
fig.add_scatter(x=DispObject.GasExplosiveCenterX, y=DispObject.GasExplosiveCenterY,mode='markers', marker=dict(size=20)) #'['none', 'tozeroy', 'tozerox', 'tonexty', 'tonextx',  'toself', 'tonext']'

fig.show()